In [1]:
from sqlalchemy import create_engine, func
import pandas as pd
pd.options.display.max_rows = 999
pd.options.display.max_columns = 999
pd.options.display.max_colwidth = 200
%ls

 Volume in drive C is Local Disk
 Volume Serial Number is 0A18-A088

 Directory of C:\Clinton Emails\final_project_2\Project_2_ETL

08/24/2019  11:46 AM    <DIR>          .
08/24/2019  11:46 AM    <DIR>          ..
08/24/2019  11:30 AM                66 .gitattributes
08/24/2019  11:46 AM    <DIR>          .ipynb_checkpoints
08/20/2019  07:38 PM        27,701,248 clinton.sqlite
08/24/2019  11:15 AM         9,775,239 Final.ipynb
08/24/2019  11:27 AM           708,608 new_db_tweets_wrd_count.sqlite
08/24/2019  11:34 AM               176 README.md
08/23/2019  08:13 PM        53,702,656 russian_bot_tweets.sqlite
08/20/2019  08:09 PM         6,291,456 tweets.sqlite
               7 File(s)     98,179,449 bytes
               3 Dir(s)  12,749,307,904 bytes free


In [2]:
# See your file path
engine = create_engine('sqlite:///clinton.sqlite')
engine_t = create_engine('sqlite:///tweets.sqlite')
engine_r = create_engine('sqlite:///russian_bot_tweets.sqlite')

In [3]:
# From Clinton email datasets
df_clinton_aliases = pd.read_sql_query('SELECT * FROM Aliases', engine)
df_clinton_emailreceiver = pd.read_sql_query('SELECT * FROM EmailReceivers', engine)
df_clinton_emails = pd.read_sql_query('SELECT * FROM Emails', engine)
df_clinton_persons = pd.read_sql_query('SELECT * FROM Persons', engine)

# From Clinton-Trump tweet datasets
df_ct_tweet = pd.read_sql('SELECT * FROM tweets', engine_t)

# From Russian tweet datasets
df_ru_tweet = pd.read_sql('SELECT * FROM tweets', engine_r)
df_ru_users = pd.read_sql('SELECT * FROM users', engine_r)

In [4]:
import re
from collections import Counter
import io 
import nltk
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize
import datetime as dt
import matplotlib.pyplot as plt

In [5]:
df_ct_tweet['time'] = pd.to_datetime(df_ct_tweet['time']).dt.strftime('%Y-%m-%d')
df_ct_tweet.sort_values('time', ascending = False)

id           handle  \
0     780925634159796224   HillaryClinton   
95    780594312182657024   HillaryClinton   
97    780593350604824576  realDonaldTrump   
98    780593298247483392  realDonaldTrump   
99    780592744355893248  realDonaldTrump   
100   780592630585499648  realDonaldTrump   
101   780592331368128512   HillaryClinton   
103   780591277620551680   HillaryClinton   
104   780591186046222336   HillaryClinton   
105   780590406501150723  realDonaldTrump   
106   780589899518967808   HillaryClinton   
107   780589488271687681   HillaryClinton   
108   780589100483145728   HillaryClinton   
109   780588840201388032   HillaryClinton   
110   780588262402424832   HillaryClinton   
111   780588035805175808   HillaryClinton   
112   780587655109181440   HillaryClinton   
96    780593967737999361   HillaryClinton   
94    780594362862362624  realDonaldTrump   
114   780586553836003333   HillaryClinton   
93    780594447427960833   HillaryClinton   
78    780602342890737664   HillaryClinton   
79    780600557325156353   HillaryClinton   
80    780600065945657344   HillaryClinton   
81    780599274384027648   HillaryClinton   
82    780598650628169729   HillaryClinton   
83    780598541441912832  realDonaldTrump   
84    780597941979480064  realDonaldTrump   
85    780597846814982144   HillaryClinton   
86    780597333650239488   HillaryClinton   
87    780596871102201856  realDonaldTrump   
88    780596663345905664   HillaryClinton   
89    780596317865254913  realDonaldTrump   
90    780595314210267137   HillaryClinton   
91    780594918616162304  realDonaldTrump   
92    780594655318638592   HillaryClinton   
113   780586814126034945   HillaryClinton   
115   780586416476676098   HillaryClinton   
76    780606012667691008   HillaryClinton   
134   780578052216676352   HillaryClinton   
136   780577456080166912   HillaryClinton   
137   780577426657120258  realDonaldTrump   
138   780577128005963776   HillaryClinton   
139   780576756713549824   HillaryClinton   
140   780576523040489472   HillaryClinton   
141   780576225848885249  realDonaldTrump   
142   780576124023762944   HillaryClinton   
143   780575993593524224   HillaryClinton   
144   780575611085582336   HillaryClinton   
145   780575331996532737   HillaryClinton   
146   780573935582707712   HillaryClinton   
147   780570465681235968   HillaryClinton   
148   780569413321789440  realDonaldTrump   
149   780565409623924736   HillaryClinton   
1     780916180899037184   HillaryClinton   
135   780577643456565248   HillaryClinton   
133   780578636294459392  realDonaldTrump   
116   780585761309659136   HillaryClinton   
132   780579514938261504   HillaryClinton   
117   780585742850555904  realDonaldTrump   
118   780585423764647936   HillaryClinton   
119   780585254583169078  realDonaldTrump   
120   780583951647768577   HillaryClinton   
121   780583741051768832  realDonaldTrump   
122   780582940732424192   HillaryClinton   
123   780582541019475968   HillaryClinton   
124   780582086231126016   HillaryClinton   
125   780581933176778752  realDonaldTrump   
126   780581355633700864   HillaryClinton   
127   780581215820591104  realDonaldTrump   
128   780580825234415616  realDonaldTrump   
129   780579923295600640  realDonaldTrump   
130   780579728964980736  realDonaldTrump   
131   780579726389809152   HillaryClinton   
77    780603720191148032   HillaryClinton   
102   780592014639456256   HillaryClinton   
75    780606592337252352   HillaryClinton   
28    780825360611086336   HillaryClinton   
21    780830984262516736   HillaryClinton   
22    780830729760485378   HillaryClinton   
23    780830087457406980   HillaryClinton   
24    780828916919504896   HillaryClinton   
25    780828206039502848   HillaryClinton   
26    780827541670076416   HillaryClinton   
27    780826236213927937  realDonaldTrump   
29    780824346310877184   HillaryClinton   
38    780802294002647040   HillaryClinton   
30    780823097498796034   HillaryClinton   
31    78081934455

In [6]:
tweet_count_df = df_ct_tweet.groupby(['handle', 'time'])['text'].count()
tweet_count_df = pd.DataFrame(tweet_count_df).reset_index()
tweet_count_df

handle        time  text
0     HillaryClinton  2016-04-17     9
1     HillaryClinton  2016-04-18    16
2     HillaryClinton  2016-04-19    17
3     HillaryClinton  2016-04-20    26
4     HillaryClinton  2016-04-21    10
5     HillaryClinton  2016-04-22    15
6     HillaryClinton  2016-04-23    13
7     HillaryClinton  2016-04-24     5
8     HillaryClinton  2016-04-25    10
9     HillaryClinton  2016-04-26    16
10    HillaryClinton  2016-04-27    40
11    HillaryClinton  2016-04-28     9
12    HillaryClinton  2016-04-29    13
13    HillaryClinton  2016-04-30     7
14    HillaryClinton  2016-05-01     7
15    HillaryClinton  2016-05-02    19
16    HillaryClinton  2016-05-03    20
17    HillaryClinton  2016-05-04    17
18    HillaryClinton  2016-05-05    20
19    HillaryClinton  2016-05-06    10
20    HillaryClinton  2016-05-07     8
21    HillaryClinton  2016-05-08     5
22    HillaryClinton  2016-05-09     9
23    HillaryClinton  2016-05-10    16
24    HillaryClinton  2016-05-11    13
25    HillaryClinton  2016-05-12    14
26    HillaryClinton  2016-05-13    11
27    HillaryClinton  2016-05-14     5
28    HillaryClinton  2016-05-15     3
29    HillaryClinton  2016-05-16    10
30    HillaryClinton  2016-05-17    11
31    HillaryClinton  2016-05-18    13
32    HillaryClinton  2016-05-19    22
33    HillaryClinton  2016-05-20    18
34    HillaryClinton  2016-05-21     8
35    HillaryClinton  2016-05-22     6
36    HillaryClinton  2016-05-23    13
37    HillaryClinton  2016-05-24    17
38    HillaryClinton  2016-05-25    15
39    HillaryClinton  2016-05-26    17
40    HillaryClinton  2016-05-27     8
41    HillaryClinton  2016-05-28     4
42    HillaryClinton  2016-05-29     4
43    HillaryClinton  2016-05-30     4
44    HillaryClinton  2016-05-31    12
45    HillaryClinton  2016-06-01    20
46    HillaryClinton  2016-06-02    21
47    HillaryClinton  2016-06-03    19
48    HillaryClinton  2016-06-04    16
49    HillaryClinton  2016-06-05    10
50    HillaryClinton  2016-06-06    10
51    HillaryClinton  2016-06-07    15
52    HillaryClinton  2016-06-08    36
53    HillaryClinton  2016-06-09    20
54    HillaryClinton  2016-06-10    25
55    HillaryClinton  2016-06-11    10
56    HillaryClinton  2016-06-12    11
57    HillaryClinton  2016-06-13    18
58    HillaryClinton  2016-06-14    27
59    HillaryClinton  2016-06-15    16
60    HillaryClinton  2016-06-16    12
61    HillaryClinton  2016-06-17    10
62    HillaryClinton  2016-06-18     7
63    HillaryClinton  2016-06-19    10
64    HillaryClinton  2016-06-20    11
65    HillaryClinton  2016-06-21    31
66    HillaryClinton  2016-06-22    28
67    HillaryClinton  2016-06-23    21
68    HillaryClinton  2016-06-24    13
69    HillaryClinton  2016-06-25     7
70    HillaryClinton  2016-06-26    21
71    HillaryClinton  2016-06-27    31
72    HillaryClinton  2016-06-28    16
73    HillaryClinton  2016-06-29    16
74    HillaryClinton  2016-06-30    13
75    HillaryClinton  2016-07-01     9
76    HillaryClinton  2016-07-02     5
77    HillaryClinton  2016-07-03     6
78    HillaryClinton  2016-07-04     6
79    HillaryClinton  2016-07-05    31
80    HillaryClinton  2016-07-06    28
81    HillaryClinton  2016-07-07    10
82    HillaryClinton  2016-07-08    18
83    HillaryClinton  2016-07-09     6
84    HillaryClinton  2016-07-10     6
85    HillaryClinton  2016-07-11    12
86    HillaryClinton  2016-07-12    38
87    HillaryClinton  2016-07-13    31
88    HillaryClinton  2016-07-14    27
89    HillaryClinton  2016-07-15    16
90    HillaryClinton  2016-07-16    15
91    HillaryClinton  2016-07-17     5
92    HillaryClinton  2016-07-18    31
93    HillaryClinton  2016-07-19    30
94    HillaryClinton  2016-07-20    30
95    HillaryClinton  2016-07-21    37
96    HillaryClinton  2016-07-22    55
97    HillaryClinton  2016-07-23    58
98    HillaryClinton  2016-07-24    12
99    HillaryClinton  2016-07-25    27
100   HillaryClinton  2016-07-26    79
101   HillaryClinton  2016-07-27    

In [7]:
df_ru_tweet

id       user_id         user_key    created_at       created_str  \
0            1  1.868981e+09    ryanmaxwell_1  1.458670e+12   3/22/2016 18:31   
1            2  2.571870e+09  detroitdailynew  1.476130e+12  10/10/2016 20:57   
2            3  1.710805e+09       cookncooks  1.487770e+12   2/22/2017 12:43   
3            4  2.584153e+09     queenofthewo  1.482760e+12  12/26/2016 15:06   
4            5  1.768260e+09     mrclydepratt  1.501990e+12     8/6/2017 2:36   
5            6  2.882014e+09      giselleevns  1.477500e+12  10/26/2016 15:33   
6            7  1.658421e+09        baobaeham  1.488910e+12    3/7/2017 18:11   
7            8  2.587101e+09   judelambertusa  1.483100e+12  12/30/2016 12:49   
8            9  1.679279e+09    ameliebaldwin  1.477790e+12   10/30/2016 1:48   
9           10  1.649488e+09        hiimkhloe  1.458160e+12   3/16/2016 19:07   
10          11  2.533002e+09       jasper_fly  1.484150e+12   1/11/2017 15:46   
11          12  2.671070e+09     patriotblake  1.481540e+12  12/12/2016 11:43   
12          13           NaN   anthonywoodboy  1.433970e+12   6/10/2015 20:33   
13          14  4.272871e+09   pamela_moore13  1.472610e+12    8/31/2016 1:49   
14          15  1.658203e+09      laurabaeley  1.485160e+12    1/23/2017 8:59   
15          16  2.882014e+09      giselleevns  1.483540e+12    1/4/2017 15:32   
16          17  4.272871e+09   pamela_moore13  1.474330e+12   9/19/2016 23:11   
17          18  1.868496e+09    brianaregland  1.484130e+12   1/11/2017 10:36   
18          19  2.590038e+09   patriotraphael  1.436750e+12    7/13/2015 1:57   
19          20  1.671235e+09          hyddrox  1.486640e+12    2/9/2017 10:26   
20          21  2.587844e+09  kansasdailynews  1.469630e+12   7/27/2016 14:55   
21          22  1.660375e+09   ilovesarahrich  1.477820e+12   10/30/2016 9:29   
22          23           NaN    evewebster373  1.427390e+12   3/26/2015 17:29   
23          24  2.671070e+09     patriotblake  1.487230e+12    2/16/2017 7:20   
24          25  7.532150e+17    margarethkurz  1.495800e+12   5/26/2017 10:59   
25          26  1.659550e+09     malloryjared  1.461350e+12   4/22/2016 17:40   
26          27  1.690488e+09     michellearry  1.458660e+12   3/22/2016 14:46   
27          28           NaN    _billy_moyer_  1.421230e+12    1/14/2015 9:00   
28          29  2.882014e+09      giselleevns  1.477050e+12  10/21/2016 12:30   
29          30  1.694026e+09  jacquelinisbest  1.478970e+12  11/12/2016 16:54   
30          31  2.540882e+09      heyits_toby  1.488260e+12    2/28/2017 5:43   
31          32  1.617939e+09        paulinett  1.492340e+12   4/16/2017 10:46   
32          33  2.882014e+09      giselleevns  1.485360e+12   1/25/2017 15:11   
33          34  2.587101e+09   judelambertusa  1.483410e+12     1/3/2017 1:19   
34          35  1.727482e+09   melvinsroberts  1.476890e+12  10/19/2016 15:03   
35          36  1.658203e+09      laurabaeley  1.485700e+12   1/29/2017 15:17   
36          37           NaN      kristyanann  1.432410e+12   5/23/2015 19:00   
37          38  1.656686e+09  jeannemccarthy0  1.482740e+12   12/26/2016 8:14   
38          39  1.684524e+09     datwisenigga  1.499930e+12    7/13/2017 7:04   
39          40  2.620870e+09        puredavie  1.473410e+12     9/9/2016 8:37   
40          41           NaN       micparrish  1.424540e+12   2/21/2015 17:24   
41          42  1.655194e+09    melanymelanin  1.464790e+12    6/1/2016 14:28   
42          43  1.617939e+09        paulinett  1.489300e+12    3/12/2017 6:57   
43          44  1.671235e+09          hyddrox  1.488700e+12     3/5/2017 7:09   
44          45  1.671235e+09          hyddrox  1.485610e+12   1/28/2017 13:08   
45          46  1.680366e+09    willisbonnerr  1.487050e+12    2/14/2017 6:40   
46          47  2.671070e+09     patriotblake  1.487330e+12   2/17/2017 11:40   
47          48  1.657754e+09      johnbranchh  1.422550e+12   1/29/2015 15:31   
48          49  1.510489e+09        lagoneh

In [8]:
russian_tweet = df_ru_tweet.rename(columns={'created_str': 'time'})

In [9]:
russian_tweet['time'] = pd.to_datetime(russian_tweet['time']).dt.strftime('%Y-%m-%d')
russian_tweet

id       user_id         user_key    created_at        time  \
0            1  1.868981e+09    ryanmaxwell_1  1.458670e+12  2016-03-22   
1            2  2.571870e+09  detroitdailynew  1.476130e+12  2016-10-10   
2            3  1.710805e+09       cookncooks  1.487770e+12  2017-02-22   
3            4  2.584153e+09     queenofthewo  1.482760e+12  2016-12-26   
4            5  1.768260e+09     mrclydepratt  1.501990e+12  2017-08-06   
5            6  2.882014e+09      giselleevns  1.477500e+12  2016-10-26   
6            7  1.658421e+09        baobaeham  1.488910e+12  2017-03-07   
7            8  2.587101e+09   judelambertusa  1.483100e+12  2016-12-30   
8            9  1.679279e+09    ameliebaldwin  1.477790e+12  2016-10-30   
9           10  1.649488e+09        hiimkhloe  1.458160e+12  2016-03-16   
10          11  2.533002e+09       jasper_fly  1.484150e+12  2017-01-11   
11          12  2.671070e+09     patriotblake  1.481540e+12  2016-12-12   
12          13           NaN   anthonywoodboy  1.433970e+12  2015-06-10   
13          14  4.272871e+09   pamela_moore13  1.472610e+12  2016-08-31   
14          15  1.658203e+09      laurabaeley  1.485160e+12  2017-01-23   
15          16  2.882014e+09      giselleevns  1.483540e+12  2017-01-04   
16          17  4.272871e+09   pamela_moore13  1.474330e+12  2016-09-19   
17          18  1.868496e+09    brianaregland  1.484130e+12  2017-01-11   
18          19  2.590038e+09   patriotraphael  1.436750e+12  2015-07-13   
19          20  1.671235e+09          hyddrox  1.486640e+12  2017-02-09   
20          21  2.587844e+09  kansasdailynews  1.469630e+12  2016-07-27   
21          22  1.660375e+09   ilovesarahrich  1.477820e+12  2016-10-30   
22          23           NaN    evewebster373  1.427390e+12  2015-03-26   
23          24  2.671070e+09     patriotblake  1.487230e+12  2017-02-16   
24          25  7.532150e+17    margarethkurz  1.495800e+12  2017-05-26   
25          26  1.659550e+09     malloryjared  1.461350e+12  2016-04-22   
26          27  1.690488e+09     michellearry  1.458660e+12  2016-03-22   
27          28           NaN    _billy_moyer_  1.421230e+12  2015-01-14   
28          29  2.882014e+09      giselleevns  1.477050e+12  2016-10-21   
29          30  1.694026e+09  jacquelinisbest  1.478970e+12  2016-11-12   
30          31  2.540882e+09      heyits_toby  1.488260e+12  2017-02-28   
31          32  1.617939e+09        paulinett  1.492340e+12  2017-04-16   
32          33  2.882014e+09      giselleevns  1.485360e+12  2017-01-25   
33          34  2.587101e+09   judelambertusa  1.483410e+12  2017-01-03   
34          35  1.727482e+09   melvinsroberts  1.476890e+12  2016-10-19   
35          36  1.658203e+09      laurabaeley  1.485700e+12  2017-01-29   
36          37           NaN      kristyanann  1.432410e+12  2015-05-23   
37          38  1.656686e+09  jeannemccarthy0  1.482740e+12  2016-12-26   
38          39  1.684524e+09     datwisenigga  1.499930e+12  2017-07-13   
39          40  2.620870e+09        puredavie  1.473410e+12  2016-09-09   
40          41           NaN       micparrish  1.424540e+12  2015-02-21   
41          42  1.655194e+09    melanymelanin  1.464790e+12  2016-06-01   
42          43  1.617939e+09        paulinett  1.489300e+12  2017-03-12   
43          44  1.671235e+09          hyddrox  1.488700e+12  2017-03-05   
44          45  1.671235e+09          hyddrox  1.485610e+12  2017-01-28   
45          46  1.680366e+09    willisbonnerr  1.487050e+12  2017-02-14   
46          47  2.671070e+09     patriotblake  1.487330e+12  2017-02-17   
47          48  1.657754e+09      johnbranchh  1.422550e+12  2015-01-29   
48          49  1.510489e+09        lagonehoe  1.477190e+12  2016-10-23   
49          50  2.572058e+09    leroylovesusa  1.447940e+12  2015-11-19   
50          51  2.584153e+09     queenofthewo  1.480350e+12  2016-11-28   
51          52  2.533654e+09       evagreen69  1.483560e+12  2017-01-04   
52          53           NaN    _bill

In [10]:
russian_tweet_df = russian_tweet
russian_tweet_df = russian_tweet_df[(russian_tweet_df['time'] >= '2016-01-05')\
                                    & (russian_tweet_df['time'] <= '2016-09-28')] 

In [11]:
russian_tweet_df.sort_values('time', ascending = True)

id       user_id         user_key    created_at        time  \
155626  155627  1.649967e+09       _nickluna_  1.452100e+12  2016-01-06   
153849  153850           NaN         c__wells  1.452110e+12  2016-01-06   
39227    39228           NaN         c__wells  1.452110e+12  2016-01-06   
201706  201707  3.990578e+09       tpartynews  1.452100e+12  2016-01-06   
38811    38812  1.690488e+09     michellearry  1.452080e+12  2016-01-06   
82251    82252  1.690488e+09     michellearry  1.452080e+12  2016-01-06   
200056  200057           NaN  jamie_mccarthy_  1.452080e+12  2016-01-06   
57379    57380  1.623180e+09   jeffreykahunas  1.452100e+12  2016-01-06   
173052  173053  3.084360e+09        mil0blake  1.452110e+12  2016-01-06   
191219  191220  3.084360e+09        mil0blake  1.452110e+12  2016-01-06   
149509  149510  2.587101e+09   judelambertusa  1.452100e+12  2016-01-06   
149536  149537  1.676481e+09      emileewaren  1.452080e+12  2016-01-06   
74173    74174  1.690488e+09     michellearry  1.452080e+12  2016-01-06   
123066  123067  3.084088e+09   priceforpierce  1.452080e+12  2016-01-06   
172685  172686  3.084360e+09        mil0blake  1.452110e+12  2016-01-06   
160386  160387  1.660771e+09  garrettsimpson_  1.452100e+12  2016-01-06   
107547  107548  3.084088e+09   priceforpierce  1.452080e+12  2016-01-06   
201567  201568  3.084088e+09   priceforpierce  1.452080e+12  2016-01-06   
39926    39927  1.649144e+09   westernwindwes  1.452080e+12  2016-01-06   
53872    53873  3.084088e+09   priceforpierce  1.452080e+12  2016-01-06   
139659  139660  1.676481e+09      emileewaren  1.452080e+12  2016-01-06   
105265  105266           NaN         c__wells  1.452110e+12  2016-01-06   
103442  103443           NaN  jamie_mccarthy_  1.452080e+12  2016-01-06   
103536  103537  1.649967e+09       _nickluna_  1.452100e+12  2016-01-06   
73371    73372  1.660771e+09  garrettsimpson_  1.452100e+12  2016-01-06   
197293  197294  1.690488e+09     michellearry  1.452080e+12  2016-01-06   
74040    74041           NaN  jamie_mccarthy_  1.452080e+12  2016-01-06   
165530  165531  1.623180e+09   jeffreykahunas  1.452100e+12  2016-01-06   
196944  196945  1.676481e+09      emileewaren  1.452080e+12  2016-01-06   
48088    48089           NaN         c__wells  1.452110e+12  2016-01-06   
19317    19318           NaN         c__wells  1.452110e+12  2016-01-06   
190220  190221  3.084360e+09        mil0blake  1.452110e+12  2016-01-06   
104581  104582  3.084360e+09        mil0blake  1.452110e+12  2016-01-06   
83003    83004  1.660771e+09  garrettsimpson_  1.452100e+12  2016-01-06   
104748  104749  1.690488e+09     michellearry  1.452080e+12  2016-01-06   
104820  104821           NaN  jamie_mccarthy_  1.452080e+12  2016-01-06   
14158    14159           NaN         c__wells  1.452110e+12  2016-01-06   
153894  153895  3.084360e+09        mil0blake  1.452110e+12  2016-01-06   
105101  105102           NaN  jamie_mccarthy_  1.452080e+12  2016-01-06   
153882  153883           NaN  jamie_mccarthy_  1.452080e+12  2016-01-06   
174538  174539           NaN       micparrish  1.452100e+12  2016-01-06   
10220    10221  2.533654e+09       evagreen69  1.452080e+12  2016-01-06   
10215    10216  1.660771e+09  garrettsimpson_  1.452100e+12  2016-01-06   
161477  161478  1.690488e+09     michellearry  1.452080e+12  2016-01-06   
54737    54738  1.649144e+09   westernwindwes  1.452080e+12  2016-01-06   
76216    76217  1.676481e+09      emileewaren  1.452080e+12  2016-01-06   
16287    16288           NaN    _billy_moyer_  1.452100e+12  2016-01-06   
167306  167307  3.084088e+09   priceforpierce  1.452080e+12  2016-01-06   
51519    51520           NaN  jamie_mccarthy_  1.452080e+12  2016-01-06   
195059  195060           NaN         c__wells  1.452110e+12  2016-01-06   
194916  194917  1.623180e+09   jeffreykahunas  1.452100e+12  2016-01-06   
68985    68986           NaN    _billy_moyer_  1.452100e+12  2016-01-06   
54699    54700  2.590038e+09   patrio

In [12]:
russian_tweet_df['handle'] = 'russian'

C:\Users\bkolinek.HELENBRETT\anaconda\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [13]:
russian_df = russian_tweet_df.groupby(['time', 'handle'])['text'].count()
russian_df = pd.DataFrame(russian_df).reset_index()
russian_df

time   handle  text
0    2016-01-06  russian   156
1    2016-01-07  russian   179
2    2016-01-08  russian    30
3    2016-01-09  russian    21
4    2016-01-10  russian   152
5    2016-01-11  russian    99
6    2016-01-12  russian    96
7    2016-01-14  russian    75
8    2016-01-15  russian   190
9    2016-01-16  russian    84
10   2016-01-17  russian   101
11   2016-01-18  russian    10
12   2016-01-19  russian    66
13   2016-01-20  russian    32
14   2016-01-21  russian    42
15   2016-01-23  russian     4
16   2016-01-24  russian    44
17   2016-01-25  russian    97
18   2016-01-26  russian    23
19   2016-01-27  russian     2
20   2016-01-28  russian    68
21   2016-01-29  russian    72
22   2016-01-30  russian     1
23   2016-02-01  russian    18
24   2016-02-02  russian    35
25   2016-02-03  russian   151
26   2016-02-04  russian   117
27   2016-02-05  russian   312
28   2016-02-06  russian   309
29   2016-02-07  russian    11
30   2016-02-08  russian   158
31   2016-02-09  russian   216
32   2016-02-10  russian   229
33   2016-02-11  russian   111
34   2016-02-12  russian     1
35   2016-02-13  russian   190
36   2016-02-14  russian   252
37   2016-02-15  russian     6
38   2016-02-16  russian    80
39   2016-02-17  russian   155
40   2016-02-18  russian   497
41   2016-02-19  russian   172
42   2016-02-20  russian   233
43   2016-02-21  russian   170
44   2016-02-22  russian   337
45   2016-02-24  russian    51
46   2016-02-25  russian   366
47   2016-02-26  russian   516
48   2016-02-28  russian     5
49   2016-02-29  russian   494
50   2016-03-01  russian   143
51   2016-03-02  russian    76
52   2016-03-03  russian     6
53   2016-03-04  russian    31
54   2016-03-05  russian   194
55   2016-03-06  russian     1
56   2016-03-07  russian    55
57   2016-03-08  russian   130
58   2016-03-09  russian   156
59   2016-03-10  russian   210
60   2016-03-11  russian    64
61   2016-03-12  russian   367
62   2016-03-13  russian    20
63   2016-03-14  russian    20
64   2016-03-15  russian    36
65   2016-03-16  russian    68
66   2016-03-17  russian   246
67   2016-03-18  russian   134
68   2016-03-19  russian    68
69   2016-03-20  russian    21
70   2016-03-21  russian    38
71   2016-03-22  russian  1021
72   2016-03-23  russian   187
73   2016-03-24  russian    48
74   2016-03-25  russian    16
75   2016-03-26  russian    11
76   2016-03-27  russian    99
77   2016-03-28  russian    25
78   2016-03-29  russian   127
79   2016-03-30  russian    16
80   2016-03-31  russian   158
81   2016-04-01  russian    29
82   2016-04-02  russian     5
83   2016-04-03  russian    19
84   2016-04-04  russian    41
85   2016-04-05  russian    15
86   2016-04-06  russian    27
87   2016-04-07  russian    63
88   2016-04-08  russian    15
89   2016-04-09  russian    48
90   2016-04-10  russian     1
91   2016-04-11  russian     1
92   2016-04-13  russian     2
93   2016-04-14  russian     1
94   2016-04-15  russian     2
95   2016-04-16  russian     4
96   2016-04-17  russian    34
97   2016-04-18  russian     7
98   2016-04-19  russian     2
99   2016-04-21  russian    19
100  2016-04-22  russian    33
101  2016-04-25  russian     4
102  2016-04-26  russian    10
103  2016-04-27  russian     9
104  2016-04-29  russian    16
105  2016-04-30  russian    36
106  2016-05-01  russian     2
107  2016-05-02  russian    12
108  2016-05-03  russian    38
109  2016-05-04  russian    31
110  2016-05-05  russian     3
111  2016-05-06  russian     1
112  2016-05-07  russian   205
113  2016-05-08  russian   357
114  2016-05-11  russian    37
115  2016-05-12  russian   281
116  2016-05-13  russian     1
117  2016-05-14  russian    13
118  2016-05-15  russian   165
119  2016-05-16  russian    57
120  2016-05-17  russian     1
121  2016-05-18  russian     2
122  2016-05-19  russian    50
123  2016-05-20  russian    35
124  2016-05-22  russian    17
125  2016-05-23  russian   116
126  2016-05-24  russian    36
127  2016-05-25  russian    12
128  2016-05

In [14]:
russian_w_words_df = russian_tweet_df.groupby(['time', 'handle'])['text']
russian_w_words_df = pd.DataFrame(russian_w_words_df).reset_index()
russian_w_words_df

index                      0  \
0        0  (2016-01-06, russian)   
1        1  (2016-01-07, russian)   
2        2  (2016-01-08, russian)   
3        3  (2016-01-09, russian)   
4        4  (2016-01-10, russian)   
5        5  (2016-01-11, russian)   
6        6  (2016-01-12, russian)   
7        7  (2016-01-14, russian)   
8        8  (2016-01-15, russian)   
9        9  (2016-01-16, russian)   
10      10  (2016-01-17, russian)   
11      11  (2016-01-18, russian)   
12      12  (2016-01-19, russian)   
13      13  (2016-01-20, russian)   
14      14  (2016-01-21, russian)   
15      15  (2016-01-23, russian)   
16      16  (2016-01-24, russian)   
17      17  (2016-01-25, russian)   
18      18  (2016-01-26, russian)   
19      19  (2016-01-27, russian)   
20      20  (2016-01-28, russian)   
21      21  (2016-01-29, russian)   
22      22  (2016-01-30, russian)   
23      23  (2016-02-01, russian)   
24      24  (2016-02-02, russian)   
25      25  (2016-02-03, russian)   
26      26  (2016-02-04, russian)   
27      27  (2016-02-05, russian)   
28      28  (2016-02-06, russian)   
29      29  (2016-02-07, russian)   
30      30  (2016-02-08, russian)   
31      31  (2016-02-09, russian)   
32      32  (2016-02-10, russian)   
33      33  (2016-02-11, russian)   
34      34  (2016-02-12, russian)   
35      35  (2016-02-13, russian)   
36      36  (2016-02-14, russian)   
37      37  (2016-02-15, russian)   
38      38  (2016-02-16, russian)   
39      39  (2016-02-17, russian)   
40      40  (2016-02-18, russian)   
41      41  (2016-02-19, russian)   
42      42  (2016-02-20, russian)   
43      43  (2016-02-21, russian)   
44      44  (2016-02-22, russian)   
45      45  (2016-02-24, russian)   
46      46  (2016-02-25, russian)   
47      47  (2016-02-26, russian)   
48      48  (2016-02-28, russian)   
49      49  (2016-02-29, russian)   
50      50  (2016-03-01, russian)   
51      51  (2016-03-02, russian)   
52      52  (2016-03-03, russian)   
53      53  (2016-03-04, russian)   
54      54  (2016-03-05, russian)   
55      55  (2016-03-06, russian)   
56      56  (2016-03-07, russian)   
57      57  (2016-03-08, russian)   
58      58  (2016-03-09, russian)   
59      59  (2016-03-10, russian)   
60      60  (2016-03-11, russian)   
61      61  (2016-03-12, russian)   
62      62  (2016-03-13, russian)   
63      63  (2016-03-14, russian)   
64      64  (2016-03-15, russian)   
65      65  (2016-03-16, russian)   
66      66  (2016-03-17, russian)   
67      67  (2016-03-18, russian)   
68      68  (2016-03-19, russian)   
69      69  (2016-03-20, russian)   
70      70  (2016-03-21, russian)   
71      71  (2016-03-22, russian)   
72      72  (2016-03-23, russian)   
73      73  (2016-03-24, russian)   
74      74  (2016-03-25, russian)   
75      75  (2016-03-26, russian)   
76      76  (2016-03-27, russian)   
77      77  (2016-03-28, russian)   
78      78  (2016-03-29, russian)   
79      79  (2016-03-30, russian)   
80      80  (2016-03-31, russian)   
81      81  (2016-04-01, russian)   
82      82  (2016-04-02, russian)   
83      83  (2016-04-03, russian)   
84      84  (2016-04-04, russian)   
85      85  (2016-04-05, russian)   
86      86  (2016-04-06, russian)   
87      87  (2016-04-07, russian)   
88      88  (2016-04-08, russian)   
89      89  (2016-04-09, russian)   
90      90  (2016-04-10, russian)   
91      91  (2016-04-11, russian)   
92      92  (2016-04-13, russian)   
93      93  (2016-04-14, russian)   
94      94  (2016-04-15, russian)   
95      95  (2016-04-16, russian)   
96      96  (2016-04-17, russian)   
97      97  (2016-04-18, russian)   
98      98  (2016-04-19, russian)   
99      99  (2016-04-21, russian)   
100    100  (2016-04-22, russian)   
101    101  (2016-04-25, russian)   
102    102  (2016-04-26, russian)   
103    103  (2016-04-27, russian)   
104    104  (2016-04-29, russian)   
105    105  (2016-04-30, russian)   
106    106  (2016-05-01, russian)   
107    10

In [23]:
combined_df = pd.merge(russian_df, tweet_count_df, how = 'left', on = 'time')
combined_df.to_csv('combine_tweet_totals.csv')
combined_df

time handle_x  text_x         handle_y  text_y
0    2016-01-06  russian     156  realDonaldTrump      18
1    2016-01-07  russian     179  realDonaldTrump      14
2    2016-01-08  russian      30  realDonaldTrump      14
3    2016-01-09  russian      21  realDonaldTrump      10
4    2016-01-10  russian     152  realDonaldTrump      13
5    2016-01-11  russian      99  realDonaldTrump      11
6    2016-01-12  russian      96  realDonaldTrump      12
7    2016-01-14  russian      75  realDonaldTrump      14
8    2016-01-15  russian     190  realDonaldTrump       5
9    2016-01-16  russian      84  realDonaldTrump      22
10   2016-01-17  russian     101  realDonaldTrump       6
11   2016-01-18  russian      10  realDonaldTrump       7
12   2016-01-19  russian      66  realDonaldTrump      17
13   2016-01-20  russian      32  realDonaldTrump      13
14   2016-01-21  russian      42  realDonaldTrump      15
15   2016-01-23  russian       4  realDonaldTrump      25
16   2016-01-24  russian      44  realDonaldTrump      19
17   2016-01-25  russian      97  realDonaldTrump      23
18   2016-01-26  russian      23  realDonaldTrump      31
19   2016-01-27  russian       2  realDonaldTrump      10
20   2016-01-28  russian      68  realDonaldTrump      33
21   2016-01-29  russian      72  realDonaldTrump      20
22   2016-01-30  russian       1  realDonaldTrump      14
23   2016-02-01  russian      18  realDonaldTrump       4
24   2016-02-02  russian      35  realDonaldTrump      16
25   2016-02-03  russian     151  realDonaldTrump      15
26   2016-02-04  russian     117  realDonaldTrump       9
27   2016-02-05  russian     312  realDonaldTrump      12
28   2016-02-06  russian     309  realDonaldTrump      20
29   2016-02-07  russian      11  realDonaldTrump      25
30   2016-02-08  russian     158  realDonaldTrump      12
31   2016-02-09  russian     216  realDonaldTrump      15
32   2016-02-10  russian     229  realDonaldTrump       9
33   2016-02-11  russian     111  realDonaldTrump      13
34   2016-02-12  russian       1  realDonaldTrump      19
35   2016-02-13  russian     190  realDonaldTrump      25
36   2016-02-14  russian     252  realDonaldTrump      21
37   2016-02-15  russian       6  realDonaldTrump       9
38   2016-02-16  russian      80  realDonaldTrump      10
39   2016-02-17  russian     155  realDonaldTrump      18
40   2016-02-18  russian     497  realDonaldTrump      14
41   2016-02-19  russian     172  realDonaldTrump      19
42   2016-02-20  russian     233  realDonaldTrump      18
43   2016-02-21  russian     170  realDonaldTrump      10
44   2016-02-22  russian     337  realDonaldTrump      18
45   2016-02-24  russian      51  realDonaldTrump      22
46   2016-02-25  russian     366  realDonaldTrump      24
47   2016-02-26  russian     516  realDonaldTrump      28
48   2016-02-28  russian       5  realDonaldTrump      28
49   2016-02-29  russian     494  realDonaldTrump      13
50   2016-03-01  russian     143  realDonaldTrump      12
51   2016-03-02  russian      76  realDonaldTrump      24
52   2016-03-03  russian       6  realDonaldTrump      19
53   2016-03-04  russian      31  realDonaldTrump      13
54   2016-03-05  russian     194  realDonaldTrump      20
55   2016-03-06  russian       1  realDonaldTrump      15
56   2016-03-07  russian      55  realDonaldTrump      14
57   2016-03-08  russian     130  realDonaldTrump      22
58   2016-03-09  russian     156  realDonaldTrump      10
59   2016-03-10  russian     210  realDonaldTrump       1
60   2016-03-11  russian      64  realDonaldTrump      16
61   2016-03-12  russian     367  realDonaldTrump      17
62   2016-03-13  russian      20  realDonaldTrump      11
63   2016-03-14  russian      20  realDonaldTrump       7
64   2016-03-15  russian      36  realDonaldTrump      29
65   2016-03-16  russian      68  realDonaldTrump      26
66   2016-03-17  russian     246  realDonaldTrump      13
67   2016-03-18  russian     134  realDonaldTrump      15
68   2016

In [16]:
hil_trump_total_text = ' '.join(df_ct_tweet['text'].tolist())
hil_trump_total_text

'The question in this election: Who can put the plans into action that will make your life better? https://t.co/XreEY9OicG Last night, Donald Trump said not paying taxes was "smart." You know what I call it? Unpatriotic. https://t.co/t0xmBfj7zF Couldn\'t be more proud of @HillaryClinton. Her vision and command during last night\'s debate showed that she\'s ready to be our next @POTUS. If we stand together, there\'s nothing we can\'t do. \n\nMake sure you\'re ready to vote: https://t.co/tTgeqxNqYm https://t.co/Q3Ymbb7UNy Both candidates were asked about how they\'d confront racial injustice. Only one had a real answer. https://t.co/sjnEokckis Join me for a 3pm rally - tomorrow at the Mid-America Center in Council Bluffs, Iowa! Tickets:… https://t.co/dfzsbICiXc This election is too important to sit out. Go to https://t.co/tTgeqxNqYm and make sure you\'re registered. #NationalVoterRegistrationDay -H When Donald Trump goes low...register to vote: https://t.co/tTgeqxNqYm https://t.co/DXz9dE

In [17]:
stop_words = set(stopwords.words('english')) 
  
word_tokens = word_tokenize(hil_trump_total_text) 
  
filtered_sentence = [w for w in word_tokens if not w in stop_words] 
  
filtered_sentence = [] 
  
for w in word_tokens: 
    if w not in stop_words: 
        filtered_sentence.append(w) 
  
#print(word_tokens) 
filtered_sentence

['The',
 'question',
 'election',
 ':',
 'Who',
 'put',
 'plans',
 'action',
 'make',
 'life',
 'better',
 '?',
 'https',
 ':',
 '//t.co/XreEY9OicG',
 'Last',
 'night',
 ',',
 'Donald',
 'Trump',
 'said',
 'paying',
 'taxes',
 '``',
 'smart',
 '.',
 "''",
 'You',
 'know',
 'I',
 'call',
 '?',
 'Unpatriotic',
 '.',
 'https',
 ':',
 '//t.co/t0xmBfj7zF',
 'Could',
 "n't",
 'proud',
 '@',
 'HillaryClinton',
 '.',
 'Her',
 'vision',
 'command',
 'last',
 'night',
 "'s",
 'debate',
 'showed',
 "'s",
 'ready',
 'next',
 '@',
 'POTUS',
 '.',
 'If',
 'stand',
 'together',
 ',',
 "'s",
 'nothing',
 'ca',
 "n't",
 '.',
 'Make',
 'sure',
 "'re",
 'ready',
 'vote',
 ':',
 'https',
 ':',
 '//t.co/tTgeqxNqYm',
 'https',
 ':',
 '//t.co/Q3Ymbb7UNy',
 'Both',
 'candidates',
 'asked',
 "'d",
 'confront',
 'racial',
 'injustice',
 '.',
 'Only',
 'one',
 'real',
 'answer',
 '.',
 'https',
 ':',
 '//t.co/sjnEokckis',
 'Join',
 '3pm',
 'rally',
 '-',
 'tomorrow',
 'Mid-America',
 'Center',
 'Council',
 'Bluf

In [18]:
from collections import Counter

In [19]:
hil_trump_word_dict = dict(Counter(filtered_sentence))
hil_trump_word_dict

{'The': 415,
 'question': 9,
 'election': 64,
 ':': 5558,
 'Who': 19,
 'put': 61,
 'plans': 26,
 'action': 17,
 'make': 223,
 'life': 57,
 'better': 89,
 '?': 366,
 'https': 4016,
 '//t.co/XreEY9OicG': 1,
 'Last': 16,
 'night': 110,
 ',': 3640,
 'Donald': 467,
 'Trump': 1232,
 'said': 124,
 'paying': 11,
 'taxes': 23,
 '``': 1523,
 'smart': 32,
 '.': 6233,
 "''": 1291,
 'You': 126,
 'know': 127,
 'I': 1313,
 'call': 28,
 'Unpatriotic': 1,
 '//t.co/t0xmBfj7zF': 1,
 'Could': 7,
 "n't": 477,
 'proud': 59,
 '@': 3045,
 'HillaryClinton': 109,
 'Her': 23,
 'vision': 11,
 'command': 1,
 'last': 129,
 "'s": 1045,
 'debate': 76,
 'showed': 10,
 'ready': 39,
 'next': 60,
 'POTUS': 164,
 'If': 137,
 'stand': 57,
 'together': 111,
 'nothing': 54,
 'ca': 101,
 'Make': 30,
 'sure': 66,
 "'re": 113,
 'vote': 173,
 '//t.co/tTgeqxNqYm': 37,
 '//t.co/Q3Ymbb7UNy': 1,
 'Both': 4,
 'candidates': 27,
 'asked': 27,
 "'d": 29,
 'confront': 3,
 'racial': 5,
 'injustice': 8,
 'Only': 15,
 'one': 241,
 'real': 5

In [20]:
import re

In [21]:
import pandas as pd

In [24]:
import string

In [25]:
df = pd.DataFrame([hil_trump_word_dict])
df_transposed = df.T
df2 = df.T.reset_index()
df2 = df2.rename(columns = {'index': 'words', 0: 'word_count'})
df2['words_updated'] = df2['words'].map(lambda x: re.sub(f'[{string.punctuation}]', '', x))
# .str.translate(",!.; -@!%^&*)(")
# df2

In [26]:
df2.drop(columns = "words", inplace=True)

In [27]:
df2['words_filtered'] = df2['words_updated'].map(lambda x: re.sub('^[^a-zA-Z]', '', x))

In [28]:
import numpy as np

In [29]:
df2['words_filtered'].replace('', np.nan, inplace=True)

In [30]:
df2.dropna(inplace=True)

In [31]:
df2.sort_values('word_count', ascending = False)

word_count          words_updated         words_filtered
12094        4016                  https                  https
6253         1313                      I                      I
8534         1232                  Trump                  Trump
53           1045                      s                      s
6174          802                Hillary                Hillary
8910          579                     We                     We
8419          487                  Thank                  Thank
13163         477                     nt                     nt
5513          467                 Donald                 Donald
14135         431        realDonaldTrump        realDonaldTrump
8428          415                    The                    The
13579         382                 people                 people
9289          360                    amp                    amp
8541          344              Trump2016              Trump2016
5176          319                Clinton                Clinton
16170         310               —Hillary                Hillary
4569          294                America                America
11795         287                  great                  great
13815         261              president              president
6877          249  MakeAmericaGreatAgain  MakeAmericaGreatAgain
6385          242                     It                     It
13349         241                    one                    one
16070         238                  would                  would
12841         223                   make                   make
15705         221                     us                     us
12676         221                   like                   like
5303          198                   Cruz                   Cruz
11693         196                    get                    get
10375         182                country                country
5293          179                Crooked                Crooked
15823         173                   vote                   vote
7236          171                    New                    New
4412          166                      A                      A
7435          164                  POTUS                  POTUS
6142          162                     He                     He
11733         161                  going                  going
13218         160                  never                  never
15390         157                  today                  today
15374         155                   time                   time
13193         155                   need                   need
16016         155                  women                  women
8461          152                   This                   This
9497          151                   back                   back
4584          147              Americans              Americans
9879          147               campaign               campaign
11386         144               families               families
4578          143               American               American
12867         141                   many                   many
6298          137                     If                     If
6035          136                  Great                  Great
8391          133                    Ted                    Ted
15881         131                   want                   want
12554         129                   last                   last
15409         129                tonight                tonight
12516         127                   know                   know
13136         126                   much                   much
9034          126                    You                    You
14496         124                   said                   said
6700          123                    Let                    Let
4455          120                AMERICA                AMERICA
11742         119                   good                   good
11750         119                    go

In [33]:
df2.to_csv('word_counts.csv')
